# Open-Unmix



__Open-Unmix__ est une implémentation de référence de réseau neuronal profond pour la séparation des sources de musique, applicable aux chercheurs, aux ingénieurs du son et aux artistes. Ce notebook fournit un accès facile à des modèles pré-entraînés qui permettent aux utilisateurs de séparer la musique pop en quatre tiges : __vocaux__, __batterie__, __basse__ et les __autres__ instruments restants. Les modèles ont été entraînés sur le jeu de données [MUSDB18](https://sigsep.github.io/datasets/musdb.html).

## Le modèle

_Open-Unmix_ est basé sur un LSTM profond bidirectionnel à trois couches. Le modèle apprend à prédire le spectrogramme de magnitude d'une cible, comme _vocals_, à partir du spectrogramme de magnitude d'un mélange en entrée. En interne, la prédiction est obtenue en appliquant un masque sur l'entrée. Le modèle est optimisé dans le domaine de l'amplitude en utilisant l'erreur quadratique moyenne et la séparation réelle est effectuée dans une étape de post-traitement impliquant un filtre de Wiener multicanal différentiable. Pour effectuer la séparation en plusieurs sources, plusieurs modèles sont formés pour chaque cible particulière. Bien que cela rende l'entraînement moins confortable, cela permet une grande flexibilité pour personnaliser les données d'entraînement pour chaque source cible.


# Installation and Imports (RUN THESE CELLS FIRST)

In [ ]:
!pip install musdb
!pip install openunmix
!pip install torchaudio
!pip install museval

     |████████████████████████████████| 963 kB 6.3 MB/s 
     |████████████████████████████████| 46 kB 1.8 MB/s 
     |████████████████████████████████| 1.9 MB 7.3 MB/s 
     |████████████████████████████████| 129 kB 5.7 MB/s 


In [ ]:
import torch
import torchaudio
import numpy as np
import scipy
#import stempeg
import os
from google.colab import files
from IPython.display import Audio, display

use_cuda = torch.cuda.is_available()
device = torch.device("cuda" if use_cuda else "cpu")

# MUSDB18 

Nous allons télécharger les 7 premieres secondes de chaque musique dans la base de données MUSDB18

In [ ]:
import musdb
mus = musdb.DB(download=True, subsets='test')

track = mus[30]
print(track.name)
display(Audio(track.audio.T, rate=track.rate))

###Appliquer la séparation en quatre tiges

open-unmix télécharge automatiquement un modèle pour chaque cible disponible :

* vocals
* drums
* bass
* other

In [ ]:
from openunmix import predict
estimates = predict.separate(
    torch.as_tensor(track.audio).float(),
    rate=track.rate,
    device=device
)   
for target, estimate in estimates.items():
    print(target)
    audio = estimate.detach().cpu().numpy()[0]
    display(Audio(audio, rate=track.rate))

print(track.name)

### Appliquer la séparation en chant/accompagnement

Même si open-unmix ne fournit pas de modèle séparé pour l'accompagnement, nous pouvons utiliser le modèle spectral `residual` dans le post-traitement pour forcer une somme linéaire de toutes les sources séparées - par exemple, ceci peut être utilisé pour la séparation chant/accompagnement. Notez que la performance de séparation est diminuée lors de l'utilisation du modèle résiduel.

In [ ]:
estimates = predict.separate(
    torch.as_tensor(track.audio).float(),
    rate=track.rate,
    targets=['vocals','drums','bass','other'], 
    residual=True,
    device=device,
)
print(track.name)
for target, estimate in estimates.items():
    print(target)
    display(Audio(estimate.detach().cpu().numpy()[0], rate=track.rate))

### Généraliser à toutes les cibles de MUSDB

Appliquons exactement la même procédure que précédemment, mais avec des éléments provenant de musdb.

Commençons par traiter la piste que nous avons chargée précédemment.

In [ ]:
from scipy.signal import stft, istft
f, t, X = stft(track.audio.T, nperseg=4096, noverlap=3072)
print(X.shape)
t, audio = istft(X, track.rate, nperseg=4096, noverlap=3072)

(2, 2049, 294)


In [ ]:
import torch
# small epsilon to avoid dividing by zero
eps = np.finfo(np.float).eps

# compute STFT of Mixture
N = track.audio.shape[0]  # remember number of samples for future use
X = stft(track.audio.T, nperseg=4096, noverlap=3072)[-1]
(I, F, T) = X.shape

# Compute sources spectrograms
P = {}
# compute model as the sum of spectrograms
model = eps

for name, source in track.sources.items():
    # compute spectrogram of target source:
    unmix = torch.hub.load('sigsep/open-unmix-pytorch', model='umx')
   # P[name] = unmix(torch.tensor(track.audio.T[None, ...]).float()).detach().numpy()[:, 0, ...].transpose(1, 2, 0)
    P[name] = np.abs(stft(source.audio.T, nperseg=4096, noverlap=3072)[-1])
    model += P[name]

# now performs separation
estimates = {}
for name, source in track.sources.items():
    # compute soft mask as the ratio between source spectrogram and total
    Mask = P[name] / model

    # multiply the mix by the mask
    Yj = Mask * X

    # invert to time domain
    target_estimate = istft(Yj, nperseg=4096, noverlap=3072)[1].T

    # set this as the source estimate
    estimates[name] = target_estimate

Downloading: "https://github.com/sigsep/open-unmix-pytorch/archive/master.zip" to /root/.cache/torch/hub/master.zip
Downloading: "https://zenodo.org/api/files/d6105b95-8c52-430c-84ce-bd14b803faaf/vocals-c8df74a5.pth" to /root/.cache/torch/hub/checkpoints/vocals-c8df74a5.pth


  0%|          | 0.00/34.0M [00:00<?, ?B/s]

Downloading: "https://zenodo.org/api/files/d6105b95-8c52-430c-84ce-bd14b803faaf/drums-5a48008b.pth" to /root/.cache/torch/hub/checkpoints/drums-5a48008b.pth


  0%|          | 0.00/34.0M [00:00<?, ?B/s]

Downloading: "https://zenodo.org/api/files/d6105b95-8c52-430c-84ce-bd14b803faaf/bass-646024d3.pth" to /root/.cache/torch/hub/checkpoints/bass-646024d3.pth


  0%|          | 0.00/34.0M [00:00<?, ?B/s]

Downloading: "https://zenodo.org/api/files/d6105b95-8c52-430c-84ce-bd14b803faaf/other-f8e132cc.pth" to /root/.cache/torch/hub/checkpoints/other-f8e132cc.pth


  0%|          | 0.00/34.0M [00:00<?, ?B/s]

Using cache found in /root/.cache/torch/hub/sigsep_open-unmix-pytorch_master
Using cache found in /root/.cache/torch/hub/sigsep_open-unmix-pytorch_master
Using cache found in /root/.cache/torch/hub/sigsep_open-unmix-pytorch_master


In [ ]:
print(track.name)
for target, estimate in estimates.items():
  display(Audio(estimate.T, rate=track.rate))

Raft Monk - Tiring


Museval permet d'évaluer les résultats de séparation de sources et d'écrire des fichiers json validés. C'est un moyen standardisé de partager les résultats de séparation de sources

In [ ]:
import museval

track_scores = museval.eval_mus_track(track, estimates)
print(track_scores)

vocals          ==> SDR:   7.496  SIR:  10.972  ISR:  10.832  SAR:  10.431  
drums           ==> SDR:   6.601  SIR:   9.297  ISR:   9.697  SAR:  10.439  
bass            ==> SDR:   5.215  SIR:   6.323  ISR:   8.384  SAR:   8.477  
other           ==> SDR:   4.760  SIR:   6.720  ISR:   8.054  SAR:   8.601  

